# Практическая работа №2. Вывод глубокой модели средствами Apache TVM. Анализ и сравнение производительности вывода

## 1. Цели и задачи работы

**Цель работы** -- изучить программный интерфейс для вывода глубоких нейросетевых
моделей, а также выполнить анализ и сравнение производительности вывода
с использованием Apache TVM и некоторых других изученных фреймворков на процессорах
архитектуры RISC-V.

Достижение указанной цели предполагает решение следующих **задач**:

1. Формулировка задачи классификации изображений.
1. Подготовка тестовых моделей для решения поставленной задачи. Изучение архитектуры
   выбранных моделей.
1. Изучение программного интерфейса Graph Execution (GE API) для вывода глубоких
   моделей фреймворка Apache TVM.
1. Программная реализация вывода выбранных моделей с использованием GE API фреймворка
   Apache TVM. Валидация корректности разработанной программной реализации.
1. Программная реализация вывода выбранных моделей с использованием других фреймворков,
   которые могут быть запущены на процессорах архитектуры RISC-V. В данной работе
   в качестве примера такого фреймворка используется TensorFlow Lite, поскольку
   на момент подготовки практической работы он оптимизирован под RISC-V-архитектуры.
1. Анализ качества решения задачи классификации с помощью выбранного набора моделей.
   При этом вывод запускается с использованием Apache TVM и TensorFlow Lite.
1. Анализ производительности вывода и определение оптимальных параметров запуска
   вывода на устройстве с процессором RISC-V (размер пачки входных данных, количество
   потоков, другие при наличии).

## 2. Постановка задачи классификации изображений

Исходное изображение, как правило, представляется набором интенсивностей пикселей

$$I=(I_{ij}^j)_{0 \le i < w, 0 \le j < h, 0 \le k < 3},$$

где $w$ и $h$ -- ширина и высота изображения, $k$ -- количество каналов,
а $I_{ij}^j$ -- значение интенсивности пикселя с пространственными координатами
$(i, j)$ по каналу $k$.

Предполагается, что определено множество наблюдаемых классов объектов на изображении:

$$C=\{0, 1,...,𝑁−1\}.$$

Множество идентификаторов классов однозначно соответствует множеству названий классов.
Таким образом, задача классификации изображений состоит в том, чтобы каждому
изображению поставить в соответствие класс, которому оно принадлежит:

$$\phi : I \rightarrow{} C.$$


## 3. Тестовые модели

### 3.1. Нейросетевая модель <НАЗВАНИЕ МОДЕЛИ 1>

<ОПИСАНИЕ МОДЕЛИ 1>

### 3.2. Нейросетевая модель <НАЗВАНИЕ МОДЕЛИ 2>

<ОПИСАНИЕ МОДЕЛИ 2>

## 4. Подготовка тестовых моделей

### 4.1. Загрузка моделей

<ОПИСАНИЕ ПРОЦЕДУРЫ ЗАГРУЗКИ МОДЕЛЕЙ>

### 4.2. Конвертация моделей в формат Apache TVM

<ОПИСАНИЕ ПРОЦЕДУРЫ КОНВЕРТАЦИИ МОДЕЛЕЙ В ФОРМАТ APACHE TVM>

### 4.3. Конвертация моделей в формат TensorFlow Lite

<ОПИСАНИЕ ПРОЦЕДУРЫ КОНВЕРТАЦИИ МОДЕЛЕЙ В ФОРМАТ TENSORFLOW LITE>

## 5. Подготовка витуальной среды для запуска экспериментов

Для проведения экспериментов необходимо подготовить виртуальную среду
с установленными пакетами `opencv` для загрузки и предварительной обработки
изображений, `apache-tvm` для вывода с использованием Apache TVM, `tensorflow`
или `tflite-runtime` для вывода средствами TensorFlow Lite. Ниже приведена
соответствующая последовательность команд.

```bash
conda create -n 02_practice_env python==3.10
conda activate 02_practice_env
conda install jupyter
conda install opencv
pip install apache-tvm
pip install tensorflow
pip install matplotlib
conda deactivate
```

Чтобы созданная виртуальная среда `02_practice_env` была доступна для последующего
запуска в ней вывода из Jupiter Notebook, достаточно в ней выполнить команду,
приведенную ниже.

```bash
conda activate 02_practice_env
python -m ipykernel install --user --name 02_practice_env \
                            --display-name "Python (02_practice_env)"
conda deactivate
```

## 6. Программная реализация вспомогательных функций

### 6.1. Функции вычисления показателей производительности

In [ ]:
# функция удаления заведомо некорректных времен
def delete_incorrect_time(times, min_correct_time=0.0):
    valid_times = []
    for i in range(len(times)):
        if times[i] >= min_correct_time:
            valid_times.append(times[i])
    return valid_times

# функция удаления времен, выходящих для пределы трех стандартных
# среднеквадратических отклонений (удаление выбросов)
def three_sigma_rule(times):
    average_time = np.mean(times)
    sigm = np.std(times)
    upper_bound = average_time + (3 * sigm)
    lower_bound = average_time - (3 * sigm)
    valid_times = []
    for i in range(len(times)):
        if lower_bound <= times[i] <= upper_bound:
            valid_times.append(times[i])
    return valid_times

# функция вычисления латентности - медианы набора корректных времен
def calculate_latency(times):
    latency = np.median(times)
    return latency

# функция вычисления метрики FPS - отношение произведения количества итераций
# и размера пачки данных к общему времени вывода
def calculate_fps(iter_num, batch_size, total_time):
    return iter_num * batch_size / total_time

# общая функция вычисления показателей производительности
def calculate_performance_metrics(times, batch_size, min_correct_time=0.0):
    valid_times = delete_incorrect_time(times, min_correct_time)
    valid_times = three_sigma_rule(valid_times)
    latency = calculate_latency(valid_times)
    fps = calculate_fps(len(valid_times), batch_size, sum(valid_times))
    return latency, fps

### 6.2. Функции обработки выхода классификационной сети

In [ ]:
# функция загрузки меток классов
def load_labels_map(labels_file_name):
    with open(labels_file_name, 'r') as f:
        labels_map = [line.strip() for line in f]
    return labels_map    

# функция печати topk-классов и соответствующих достоверностей
def process_output(files, output_data, labels_file_name, topk=5):
    labels_map = load_labels_map(labels_file_name)
    for i in range(len(output_data)):
        file_name = files[i]
        probs_ = np.squeeze(output_data[i])
        top_ind = np.argsort(probs_)[-topk:][::-1]
        print(f'{file_name}')
        for id_ in top_ind:
            det_label = labels_map[id_] if labels_map else '#{0}'.format(id_)
            print('\t{}\t{:.7f}\t{}'.format(id_, probs_[id_], det_label))

### 6.3. Чтение и предварительная обработка данных

Для чтения и подготовки изображений используется функционал библиотеки компьютерного
зрения OpenCV:

1. `cv2.imread(...)` -- функция, обеспечивающая загрузку изображения.
1. `cv2.resize(...)` -- функция, обеспечивающая масштабирование изображения
   в соответствии с размерами входного тензора нейронной сети.
1. <ВСТАВИТЬ ДРУГИЕ ФУНКЦИИ, КОТОРЫЕ ИСПОЛЬЗУЮТСЯ ДЛЯ ПРЕДВАРИТЕЛЬНОЙ ОБРАБОТКИ>

<ОПИСАНИЕ НАБОРА ДАННЫХ, КОТОРЫЙ ИСПОЛЬЗУЕТСЯ ДЛЯ ТЕСТИРОВАНИЯ>

In [ ]:
def prepare_input(images_dir, input_image_resolution, mean=(0, 0, 0),
                  scale=(1, 1, 1), bgr_to_rgb=False, show=False):
    files = [f for f in os.listdir(images_dir) if os.path.isfile(os.path.join(images_dir, f))]
    print(f'Number of available images: {len(files)}')
    images = []
    # <ВСТАВИТЬ ЧТЕНИЕ И ОБРАБОТКУ ИЗОБРАЖЕНИЙ>
    return files, images

## 7. Программная реализация вывода средствами Apache TVM

Программная реализация вывода средствами фреймворка Apache TVM выполняется
с использованием Graph Execution API (GE API).

### 7.1. Загрузка пакетов

In [ ]:
# <ЗАГРУЗКА НЕОБХОДИМЫХ ПАКЕТОВ>

### 7.2. Загрузка и предварительная обработка данных

In [ ]:
# <ВЫЗОВ ФУНКЦИИ PREPARE_INPUT(...) ДЛЯ ЗАГРУЗКИ И ПРЕДВАРИТЕЛЬНОЙ ОБРАБОТКИ ИЗОБРАЖЕНИЙ>

### 7.3. Загрузка скомпилированной модели

In [ ]:
# <ЗАГРУЗКА СКОМПИЛИРОВАННОЙ МОДЕЛИ СРЕДСТВАМИ GE API>

### 7.4. Вывод нейронной сети

In [ ]:
# количество повторений запуска вывода
iter_num = 100
# размер пачки данных
batch_size = 4

# функция многократного запуска вывода для фиксированного размера пачки
# и сбор результатов работы сети и времени работы каждого запроса на вывод
def inference(iter_num, batch_size, files, images):
    # список времен вывода для набора итераций
    times = []
    # словарь результатов вывода (ключ - название файла изображения,
    # значение - вектор достоверностей)
    results = dict()
    # из множества изображений организуется кольцевой буфер
    # индексы начального и конечного изображения в пачке данных
    istart = 0
    ifinish = batch_size
    for iteration in range(iter_num):
        # <ЗАПУСК ВЫВОДА ДЛЯ ПАЧКИ ИЗОБРАЖЕНИЙ>
        # <СОХРАНЕНИЕ РЕЗУЛЬТАТОВ ВЫВОДА В СЛОВАРЬ>
        # <СОХРАНЕНИЕ ВРЕМЕНИ ВЫВОДА В СПИСОК ВРЕМЕН>

        # пересчет индексов начального и конечного изображений для новой пачки
        istart = ifinish
        ifinish = (istart + batch_size) % (len(images) + 1)
        if istart > ifinish:
            istart = 0
            ifinish = batch_size
        
    return results, times

# функция запуска теста и вычисления показателей производительности вывода
def inference_tvm_perf(iter_num, batch_size, files, images):
    results, times = inference(iter_num, batch_size, files, images)
    latency, fps = calculate_performance_metrics(times, batch_size)
    return results, latency, fps


results, latency, fps = inference_tvm_perf(iter_num, batch_size, files, images)
print('Performance metrics:')
print(f'\tLatency: {latency:.3f} s\n\tFPS:     {fps:.2f} fps')

print('Results:')
for iteration in range(len(results)):
    process_output(results[iteration][0], results[iteration][1], labels_file_name, topk)

## 8. Программная реализация вывода средствами TensorFlow Lite

### 8.1. Загрузка пакетов

In [ ]:
# <ЗАГРУЗКА НЕОБХОДИМЫХ ПАКЕТОВ>

### 8.2. Загрузка и предварительная обработка данных

In [ ]:
# <ВЫЗОВ ФУНКЦИИ PREPARE_INPUT(...) ДЛЯ ЗАГРУЗКИ И ПРЕДВАРИТЕЛЬНОЙ ОБРАБОТКИ ИЗОБРАЖЕНИЙ>

### 8.3. Загрузка модели

In [ ]:
# <ЗАГРУЗКА МОДЕЛИ>

### 8.4. Установка входных тензоров и запуск вывода

In [ ]:
# <РЕАЛИЗАЦИЯ ВЫВОДА ПО АНАЛОГИИ С ТЕМ, КАК ЭТО СДЕЛАНО ДЛЯ APACHE TVM>

## 9. Анализ качества решения задачи классификации

**Инструменты для сбора показателей качества.** <ОПИСАНИЕ ИСПОЛЬЗУЕМЫХ ИНСТРУМЕНТОВ>

**Набор данных.** <ОПИСАНИЕ НАБОРА ДАННЫХ>

**Показатели качества.** <ОПИСАНИЕ ПОКАЗАТЕЛЯ КАЧЕСТВА>

**Последовательность подготовки окружения и сбора показателей качества.** <ОПИСАНИЕ ПРОЦЕДУРЫ СБОРА ПОКАЗАТЕЛЕЙ КАЧЕСТВА>

In [ ]:
# <ОТОБРАЖЕНИЕ ГИСТОГРАММЫ С ПОЛУЧЕННЫМИ РЕЗУЛЬТАТАМИ КАЧЕСТВА РЕШЕНИЯ ЗАДАЧИ КЛАССИФИКАЦИИ>
# <НЕОБХОДИМО ПОКАЗАТЬ РЕЗУЛЬТАТЫ ДЛЯ APACHE TVM, TENSORFLOW LITE И РЕФЕНСНЫЕ ПОКАЗАТЕЛИ КАЧЕСТВА>

## 10. Анализ и сравнение производительности вывода на RISC-V

### 10.1. Параметры тестовой инфраструктуры

В данной работе для получения информации о тестовой инфраструктуре используются
функции, входящие в состав стандартных пакетов Python.

In [ ]:
import os
import platform
import subprocess
import re
from collections import OrderedDict
from sys import version as python_formatted_version


def get_cpu_name():
    cpuname = 'Undefined'

    if platform.system() == 'Windows':
        return platform.processor()    
    elif platform.system() == 'Linux':
        command = 'cat /proc/cpuinfo'
        all_info = subprocess.check_output(command, shell=True).decode().strip()
        for line in all_info.split('\n'):
            if 'model name' in line:
                return re.sub( ".*model name.*: ", "", line, 1)

    return cpuname.strip()

def get_ram_size(ostype):
    ramsize = 'Undefined'
    if ostype == 'Windows':
        command = ['wmic', 'OS', 'get', 'TotalVisibleMemorySize', '/Value']
        p = subprocess.Popen(command, universal_newlines=True, shell=True,
                             stdout=subprocess.PIPE, stderr=subprocess.PIPE)
        text = p.stdout.read()
        p.wait()
        text = text.split('=')
        ramsize = text[1].strip() + ' KB'
    elif ostype == 'Linux':
        command = ['cat', '/proc/meminfo']
        all_info = subprocess.check_output(command).strip().decode()
        for line in all_info.split('\n'):
            if 'MemTotal' in line:
                return line.split(':')[1].strip()
    return ramsize

def get_system_characteristics():
    ostype = platform.system()
    characteristics = OrderedDict()
    characteristics.update({'CPU': get_cpu_name()})
    characteristics.update({'Number of CPUs': os.cpu_count()})
    characteristics.update({'CPU family': platform.processor()})
    characteristics.update({'RAM size': get_ram_size(ostype)})
    characteristics.update({'OS family': platform.system()})
    characteristics.update({'OS version': platform.platform()})
    characteristics.update({'Python version': python_formatted_version})

    return characteristics


hardware_dict = get_system_characteristics()
for key, value in hardware_dict.items():
    print(f'{key:16}: {value}')

### 10.2. Параметры для определения оптимальной производительности вывода

In [ ]:
# размеры входных пачек данных
batch_sizes = [1, 2, 4, 8, 16]
# количество итераций для определения показателей латентности и FPS
iter_num = 50

# количество потоков для вывода средствами TensorFlow Lite
num_threads = [1, 2, 4, 8, 16, 32]

# уровни оптимизации моделей Apache TVM
opt_levels = [0, 1, 2, 3]

### 10.3. Определение оптимальных параметров вывода с использованием Apache TVM

In [ ]:
# <РЕАЛИЗОВАТЬ ФУНКЦИЮ ЗАПУСКА ТЕСТОВ ПРОИЗВОДИТЕЛЬНОСТИ ДЛЯ РАЗНЫХ РАЗМЕРОВ ВХОДНЫХ ПАЧЕК ДАННЫХ>

Для наглядности полученных результатов построим на одной диаграмме
графики зависимости FPS от размера пачки входных данных для каждого
фиксированного уровня оптимизации модели.

In [ ]:
# <ОТОБРАЖЕНИЕ ГРАФИКА ЗАВИСИМОСТИ FPS ОТ РАЗМЕРА ПАЧКИ ДАННЫХ ДЛЯ РАЗНЫХ ПАРАМЕТРОВ ЗАПУСКА ВЫВОДА>

**Выводы из построенных графиков**: <ДОБАВИТЬ ВЫВОДЫ>

### 10.4. Определение оптимальных параметров вывода с использованием TensorFlow Lite

In [ ]:
# <РЕАЛИЗОВАТЬ ФУНКЦИЮ ЗАПУСКА ТЕСТОВ ПРОИЗВОДИТЕЛЬНОСТИ ДЛЯ РАЗНЫХ РАЗМЕРОВ ВХОДНЫХ ПАЧЕК ДАННЫХ>

Для наглядности полученных результатов построим на одной диаграмме
графики зависимости FPS от размера входной пачки данных при разных
значениях числа потоков.

In [ ]:
# <ОТОБРАЖЕНИЕ ГРАФИКА ЗАВИСИМОСТИ FPS ОТ РАЗМЕРА ПАЧКИ ДАННЫХ ДЛЯ РАЗНЫХ ПАРАМЕТРОВ ЗАПУСКА ВЫВОДА>

**Вывода из построенных графиков:** <ДОБАВИТЬ ВЫВОДЫ>

### 10.5. Сравнение показателей производительности

In [ ]:
# <ВЫБОР ЛУЧШИХ ПОКАЗАТЕЛЕЙ ПРОИЗВОДИТЕЛЬНОСТИ ДЛЯ КАЖДОГО ФРЕЙМВОРКА>

**Выводы:** <ДОБАВИТЬ ВЫВОДЫ>